#### Génération du graph "routier" dans Neo4J

##### PARTIE 1 : CONSTRUCTION DU GRAPH ET CALCUL DU BETWEENESS

Notebook amorcé par : Jesshuan

Objectifs :

- Récupération du graph sous forme edges et nodes depuis les notebooks de mika...

- Génération dans une base de données locale Neo4j

#### Echec de la génération... nosu avons trouvé finalement une autre solution avec un simple transfert de fichier de format osm à format neo4j

Imports :

In [1]:
import geopandas as gpd
import pandas as pd
import geopy.distance
import os
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import copy
import joblib

from neo4j import GraphDatabase, basic_auth

In [2]:
PASSWORD_NEO4J = 'passwordneo4j'

--------

In [3]:
class CFG:
    area = [
        'Auvergne-Rhône-Alpes',
    'Bourgogne-Franche-Comté',
    'Brittany',
    'Centre-Val de Loire',
    'Grand Est',
    'Hauts-de-France',
    'Île-de-France',
    'Normandie',
    'Nouvelle-Aquitaine',
    'Occitanie',
    'Pays de la Loire',
    'Provence-Alpes-Côte d\'Azur'
]
    area_name = 'france'      #'_'.join(area)

    

    bornes = False

    viz = False

    roads = (
        '|motorway'
        '|motorway_link'
        '|trunk'
        '|trunk_link'
        '|primary'
        '|primary_link'
        '|secondary'
        '|secondary_link'
        '|tertiary'
         '|tertiary_link'
    )

        # '|primary'
        # '|motorway_link'
        
        # '|primary_link'

        # '|secondary'
        # '|secondary_link'
        
        
        #  '|tertiary'
        #  '|tertiary_link'

    data_path = './osm_datas/'

import joblib
joblib.dump(CFG.area, 'CFG.pkl')    
import os
os.environ['USE_PYGEOS'] = '0'
%load_ext autoreload
%autoreload



%aimport OSM_helper_functions
%aimport OCM_helper_functions

import os
os.environ['USE_PYGEOS'] = '0'
import geopandas as gpd
import osmnx as ox
import networkx as nx
from tqdm.notebook import tqdm
from OSM_helper_functions import *
from OCM_helper_functions import *


ox.settings.log_console=True
ox.settings.use_cache=True
''' To retrieve http data from OSMnx and cache them locally
    before building graph. Raise and exception if requests
    are all done. intercept then set to False and retry.'''
# ox.settings.cache_only_mode=True 

Administratives = {
    'Auvergne-Rhône-Alpes': ['Ain', 'Allier', 'Ardèche', 'Cantal', 'Drôme', 'Isère', 'Loire', 'Haute-Loire', 'Puy-de-Dôme', 'Rhône', 'Savoie', 'Haute-Savoie'],
    'Bourgogne-Franche-Comté': ['Côte-d\'Or', 'Doubs', 'Jura', 'Nièvre', 'Haute-Saône', 'Saône-et-Loire', 'Yonne', 'Territoire de Belfort'],
    'Brittany': ['Côtes-d\'Armor', 'Finistère', 'Ille-et-Vilaine', 'Morbihan'],
    'Centre-Val de Loire': ['Cher', 'Eure-et-Loir', 'Indre', 'Indre-et-Loire', 'Loir-et-Cher', 'Loiret'],
    # 'Corse': ['Corse-du-Sud', 'Haute-Corse'],
    'Grand Est': ['Ardennes', 'Aube', 'Marne', 'Haute-Marne', 'Meurthe-et-Moselle', 'Meuse', 'Moselle', 'Bas-Rhin', 'Haut-Rhin', 'Vosges'],
    'Hauts-de-France': ['Aisne', 'Nord', 'Oise', 'Pas-de-Calais', 'Somme'],
    'Île-de-France': ['Paris', 'Seine-et-Marne', 'Yvelines', 'Essonne', 'Hauts-de-Seine', 'Seine-Saint-Denis', 'Val-de-Marne', 'Val-d\'Oise'],
    'Normandie': ['Calvados', 'Eure', 'Manche', 'Orne', 'Seine-Maritime'],
    'Nouvelle-Aquitaine': ['Charente', 'Charente-Maritime', 'Corrèze', 'Creuse', 'Dordogne', 'Gironde', 'Landes', 'Lot-et-Garonne', 'Pyrénées-Atlantiques', 'Deux-Sèvres', 'Vienne', 'Haute-Vienne'],
    'Occitanie': ['Ariège', 'Aude', 'Aveyron', 'Gard', 'Haute-Garonne', 'Gers', 'Hérault', 'Lot', 'Lozère', 'Hautes-Pyrénées', 'Pyrénées-Orientales', 'Tarn', 'Tarn-et-Garonne'],
    'Pays de la Loire': ['Loire-Atlantique', 'Maine-et-Loire', 'Mayenne', 'Sarthe', 'Vendée'],
    'Provence-Alpes-Côte d\'Azur': ['Alpes-de-Haute-Provence', 'Hautes-Alpes', 'Alpes-Maritimes', 'Bouches-du-Rhône', 'Var', 'Vaucluse']
}

Regions = [
    'Auvergne-Rhône-Alpes',
    'Bourgogne-Franche-Comté',
    'Brittany',
    'Centre-Val de Loire',
    # 'Corse',
    'Grand Est',
    'Hauts-de-France',
    'Île-de-France',
    'Normandie',
    'Nouvelle-Aquitaine',
    'Occitanie',
    'Pays de la Loire',
    'Provence-Alpes-Côte d\'Azur'
]

Name2num = {
    'Ain': '01',
    'Aisne': '02',
    'Allier': '03',
    'Alpes-de-Haute-Provence': '04',
    'Hautes-Alpes': '05',
    'Alpes-Maritimes': '06',
    'Ardèche': '07',
    'Ardennes': '08',
    'Ariège': '09',
    'Aube': '10',
    'Aude': '11',
    'Aveyron': '12',
    'Bouches-du-Rhône': '13',
    'Calvados': '14',
    'Cantal': '15',
    'Charente': '16',
    'Charente-Maritime': '17',
    'Cher': '18',
    'Corrèze': '19',
    # 'Corse-du-Sud': '2A',
    # 'Haute-Corse': '2B',
    'Côte-d\'Or': '21',
    'Côtes-d\'Armor': '22',
    'Creuse': '23',
    'Dordogne': '24',
    'Doubs': '25',
    'Drôme': '26',
    'Eure': '27',
    'Eure-et-Loir': '28',
    'Finistère': '29',
    'Gard': '30',
    'Haute-Garonne': '31',
    'Gers': '32',
    'Gironde': '33',
    'Hérault': '34',
    'Ille-et-Vilaine': '35',
    'Indre': '36',
    'Indre-et-Loire': '37',
    'Isère': '38',
    'Jura': '39',
    'Landes': '40',
    'Loir-et-Cher': '41',
    'Loire': '42',
    'Haute-Loire': '43',
    'Loire-Atlantique': '44',
    'Loiret': '45',
    'Lot': '46',
    'Lot-et-Garonne': '47',
    'Lozère': '48',
    'Maine-et-Loire': '49',
    'Manche': '50',
    'Marne': '51',
    'Haute-Marne': '52',
    'Mayenne': '53',
    'Meurthe-et-Moselle': '54',
    'Meuse': '55',
    'Morbihan': '56',
    'Moselle': '57',
    'Nièvre': '58',
    'Nord': '59',
    'Oise': '60',
    'Orne': '61',
    'Pas-de-Calais': '62',
    'Puy-de-Dôme': '63',
    'Pyrénées-Atlantiques': '64',
    'Hautes-Pyrénées': '65',
    'Pyrénées-Orientales': '66',
    'Bas-Rhin': '67',
    'Haut-Rhin': '68',
    'Rhône': '69',
    'Haute-Saône': '70',
    'Saône-et-Loire': '71',
    'Sarthe': '72',
    'Savoie': '73',
    'Haute-Savoie': '74',
    'Paris': '75',
    'Seine-Maritime': '76',
    'Seine-et-Marne': '77',
    'Yvelines': '78',
    'Deux-Sèvres': '79',
    'Somme': '80',
    'Tarn': '81',
    'Tarn-et-Garonne': '82',
    'Var': '83',
    'Vaucluse': '84',
    'Vendée': '85',
    'Vienne': '86',
    'Haute-Vienne': '87',
    'Vosges': '88',
    'Yonne': '89',
    'Territoire de Belfort': '90',
    'Essonne': '91',
    'Hauts-de-Seine': '92',
    'Seine-Saint-Denis': '93',
    'Val-de-Marne': '94',
    'Val-d\'Oise': '95'
}


AREA = []
for area in CFG.area:
    AREA.extend(Administratives[area] )
AREA

['Ain',
 'Allier',
 'Ardèche',
 'Cantal',
 'Drôme',
 'Isère',
 'Loire',
 'Haute-Loire',
 'Puy-de-Dôme',
 'Rhône',
 'Savoie',
 'Haute-Savoie',
 "Côte-d'Or",
 'Doubs',
 'Jura',
 'Nièvre',
 'Haute-Saône',
 'Saône-et-Loire',
 'Yonne',
 'Territoire de Belfort',
 "Côtes-d'Armor",
 'Finistère',
 'Ille-et-Vilaine',
 'Morbihan',
 'Cher',
 'Eure-et-Loir',
 'Indre',
 'Indre-et-Loire',
 'Loir-et-Cher',
 'Loiret',
 'Ardennes',
 'Aube',
 'Marne',
 'Haute-Marne',
 'Meurthe-et-Moselle',
 'Meuse',
 'Moselle',
 'Bas-Rhin',
 'Haut-Rhin',
 'Vosges',
 'Aisne',
 'Nord',
 'Oise',
 'Pas-de-Calais',
 'Somme',
 'Paris',
 'Seine-et-Marne',
 'Yvelines',
 'Essonne',
 'Hauts-de-Seine',
 'Seine-Saint-Denis',
 'Val-de-Marne',
 "Val-d'Oise",
 'Calvados',
 'Eure',
 'Manche',
 'Orne',
 'Seine-Maritime',
 'Charente',
 'Charente-Maritime',
 'Corrèze',
 'Creuse',
 'Dordogne',
 'Gironde',
 'Landes',
 'Lot-et-Garonne',
 'Pyrénées-Atlantiques',
 'Deux-Sèvres',
 'Vienne',
 'Haute-Vienne',
 'Ariège',
 'Aude',
 'Aveyron',
 'Gard

In [4]:
nodes = joblib.load( os.path.join(CFG.data_path, f'[{CFG.area_name}]Gnodes.pkl'))

edges = joblib.load( os.path.join(CFG.data_path, f'[{CFG.area_name}]Gedges.pkl'))

--------------------------

Fonctions de requêtes neo4j :

In [5]:
def delete_all(tx):
    query = 'MATCH (n) \
                DETACH DELETE n \
                RETURN count(*) AS COUNT'
    result = tx.run(query)
    return result.data()

In [56]:
def delete_just_edges(tx):
    query = 'MATCH ()-[r]-() \
                DELETE r \
                RETURN count(*) AS COUNT'
    result = tx.run(query)
    return result.data()

In [8]:
def create_node(tx, node):
    query = "   WITH $node AS node \
                CREATE (r:ROAD {road_index:node}) \
                RETURN count(r) AS COUNT"
    
    result = tx.run(query, node=node)
    return result.data()

In [24]:
def create_node_ROAD_POINT_per_batch(tx, props_list):

    query = "   UNWIND $props_list AS map \
                CREATE (n:ROAD_POINT) \
                SET n = map \
                RETURN count(n) AS COUNT"

    result = tx.run(query, props_list=props_list)
    return result.data()

In [45]:
def create_edge_between_ROAD_POINTS(tx, props_list):

    query = "   UNWIND $props_list AS map \
                MERGE (n1:ROAD_POINT {osmid : map.u})-[r:CONNECT]->(n2:ROAD_POINT {osmid : map.v}) \
                SET r = map \
                RETURN count(r) AS COUNT"

    result = tx.run(query, props_list=props_list)
    return result.data()

In [8]:
def check_collection(tx, id):

    query = "  WITH $id AS id \
                MATCH (n) \
                WHERE n.osmid = id \
                RETURN count(n) \
                 "
    
    result = tx.run(query, id=id)
    return result.data()

In [7]:
def assign_label_ROAD_POINT(tx):

    query = "   MATCH (n) \
                WHERE n.street_count IS NOT NULL \
                SET n :ROAD_POINT \
                RETURN count(n) \
                 "
    
    result = tx.run(query)
    return result.data()

In [7]:
def all_fusion_nodes(tx, id):

    query = "   WITH $id AS id \
                MATCH (n) \
                WHERE n.osmid = id \
                WITH collect(n) AS nodes \
                CALL apoc.refactor.mergeNodes( \
                                        nodes, \
                                        {properties: { \
                                        osmid: 'discard', \
                                        `.*`:'combine'} \
                                            }) \
                YIELD node \
                RETURN node "
    
    result = tx.run(query,  id=id)
    return result.data()

In [25]:
def match_alone_nodes(tx):
    query = " MATCH (r) \
            WHERE NOT (r)-[:LINKED_TO]-() \
            RETURN r.road_index AS road_index"
    
    result = tx.run(query)
    return result.data()

Drivers session for Neo4j :

In [5]:
driver = GraphDatabase.driver(
  "bolt://localhost:7687",
  auth=basic_auth("neo4j", PASSWORD_NEO4J))

Ardoise (pour effacer tout ancien graph)

In [40]:
with driver.session() as session:

    count_list = []

    result = session.execute_write(delete_all)

driver.close()

nb_nodes = result[0]['COUNT']
                
print(f'Total Numbers of deleted nodes: {nb_nodes}')

Total Numbers of deleted nodes: 2


Ardoise (pour effacer seulement les relations)

In [158]:
with driver.session() as session:

    count_list = []

    result = session.execute_write(delete_just_edges)

driver.close()

nb_edges = result[0]['COUNT']
                
print(f'Total Numbers of deleted edges: {nb_edges}')

Total Numbers of deleted edges: 0


---

NODES GENERATION :

In [12]:
nodes.describe(include='all')

y              x   street_count            highway   ref   
count   523308.000000  523308.000000  523308.000000              21297  4151  \
unique            NaN            NaN            NaN                 19   324   
top               NaN            NaN            NaN  motorway_junction     5   
freq              NaN            NaN            NaN               7304   141   
mean        46.847334       2.285751       3.007758                NaN   NaN   
std          2.225038       2.824368       0.412084                NaN   NaN   
min         42.358381      -4.780139       1.000000                NaN   NaN   
25%         44.922946       0.100040       3.000000                NaN   NaN   
50%         47.231357       2.360317       3.000000                NaN   NaN   
75%         48.714446       4.633116       3.000000                NaN   NaN   
max         51.078833       8.205845      16.000000                NaN   NaN   

                            geometry  
count                         523308  
unique                        523307  
top     POINT (-1.993727 48.6555579)  
freq                               2  
mean                             NaN  
std                              NaN  
min                              NaN  
25%                              NaN  
50%                              NaN  
75%                              NaN  
max                              NaN

In [13]:
nodes['highway'].value_counts()

highway
motorway_junction    7304
crossing             6770
traffic_signals      4872
mini_roundabout      1664
bus_stop              391
milestone              80
give_way               69
stop                   65
turning_circle         55
services                6
passing_place           4
mini_circular           4
trailhead               4
rest_area               2
turning_loop            2
speed_display           2
priority                1
emergency_bay           1
construction            1
Name: count, dtype: int64

In [65]:
nodes_reset = nodes.reset_index()

In [66]:
nodes_reset.drop(['geometry'], axis=1, inplace=True)

In [16]:
primary_key = 'osmid'
object_entity = 'ROAD_POINT'

In [26]:
#nodes_reset.fillna('nan', inplace=True)
#nodes_reset = nodes_reset.loc[nodes_reset[primary_key]!='nan', :]

In [21]:
#nodes_reset = nodes_reset.iloc[220000:]

In [ ]:
print("conversion of objects to parameters list for neo4j...")

props_list = nodes_reset.to_dict("records")

conversion of objects to parameters list for neo4j...


In [28]:
BATCH_SIZE = 20000

In [ ]:
# --- Batch function ---

def batch(iterable, n=1):
    l = len(iterable)
    for ndx in range(0, l, n):
        yield iterable[ndx:min(ndx + n, l)]


In [25]:
with driver.session() as session:

    count_list = []

    # Batch the writing session :

    for props_batch in batch(props_list, BATCH_SIZE):
        result = session.write_transaction(create_node_ROAD_POINT_per_batch, props_batch)
        count_list.append(result[0]['COUNT'])
        nb_updates = sum(count_list)
        print(f'Number of nodes created : {nb_updates}...')

        

    driver.close()

print(f'Bath_list: {count_list}')

print(f'Total Numbers of nodes created/updates: {nb_updates}')

/tmp/ipykernel_29640/1815704222.py:8: DeprecationWarning: write_transaction has been renamed to execute_write
  result = session.write_transaction(create_node_ROAD_POINT_per_batch, props_batch)


Number of nodes created : 10000...
Number of nodes created : 20000...
Number of nodes created : 30000...
Number of nodes created : 40000...
Number of nodes created : 50000...
Number of nodes created : 60000...
Number of nodes created : 70000...
Number of nodes created : 80000...
Number of nodes created : 90000...
Number of nodes created : 100000...
Number of nodes created : 110000...
Number of nodes created : 120000...
Number of nodes created : 130000...
Number of nodes created : 140000...
Number of nodes created : 150000...
Number of nodes created : 160000...
Number of nodes created : 170000...
Number of nodes created : 180000...
Number of nodes created : 190000...
Number of nodes created : 200000...
Number of nodes created : 210000...
Number of nodes created : 220000...
Number of nodes created : 230000...
Number of nodes created : 240000...
Number of nodes created : 250000...
Number of nodes created : 260000...
Number of nodes created : 270000...
Number of nodes created : 280000...
N

---

EDGES GENERATION :

In [ ]:
edges.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
MultiIndex: 1066293 entries, (27174280, 27174283, 0) to (10951141937, 9970850094, 0)
Data columns (total 20 columns):
 #   Column       Non-Null Count    Dtype   
---  ------       --------------    -----   
 0   osmid        1066293 non-null  object  
 1   lanes        304052 non-null   object  
 2   ref          675525 non-null   object  
 3   name         644069 non-null   object  
 4   highway      1066293 non-null  object  
 5   oneway       1066293 non-null  object  
 6   reversed     1066293 non-null  object  
 7   length       1066293 non-null  float64 
 8   speed_kph    1066293 non-null  object  
 9   travel_time  1066293 non-null  float64 
 10  geometry     1066293 non-null  geometry
 11  bridge       106844 non-null   object  
 12  maxspeed     482828 non-null   object  
 13  access       9686 non-null     object  
 14  junction     182384 non-null   object  
 15  width        5287 non-null     object  
 16  tunnel       6086 non

In [11]:
edges_reset = edges.reset_index()
edges_reset.drop(['geometry', 'key'], axis=1, inplace=True)

In [12]:
already_viewed = set()

u_list = edges_reset['u'].tolist()
v_list = edges_reset['v'].tolist()

keep_list = []

for u, v in zip(u_list, v_list):
    if (u, v) in already_viewed:
        keep_list.append(False)
    else:
        keep_list.append(True)
        already_viewed.add((u, v))
        already_viewed.add((v, u))

edges_reset['keep'] = keep_list


In [13]:
edges_reset = edges_reset.loc[edges_reset['keep']==True,:]

In [103]:
u_categories = edges_reset['u'].value_counts()

In [104]:
fig = px.histogram(u_categories)
fig.show()

In [14]:
edges_reset.sort_values(['u','v'], inplace=True)

In [15]:
edges_reset.drop(['keep'], axis=1, inplace=True)

In [16]:
edges_reset

u            v   
579108       122631    700952720  \
579109       122639    130594034   
41800        122859       655430   
569837       122926    318399738   
569838       122935     85245595   
...             ...          ...   
668691  10978436860  10978436863   
400380  10978514666    248499149   
400381  10978514666    500561487   
125491  10978946614  10978946623   
123852  10979049286   6937930122   

                                                    osmid      lanes     ref   
579108                                          682853120          4     A 1  \
579109                                          682853112          4     A 1   
41800                                            23285191          2   N 532   
569837  [332409156, 39750470, 39750471, 1105411815, 42...  [5, 4, 3]     A 3   
569838                   [35305692, 377981558, 109067639]          5     A 3   
...                                                   ...        ...     ...   
668691                                         1182191887        NaN    D336   
400380                                         1182198460          1     NaN   
400381                                         1182198461        NaN     NaN   
125491                                         1182256798        NaN  D 1205   
123852                                          741058299        NaN     NaN   

                     name     highway oneway reversed    length  ...   
579108  Autoroute du Nord    motorway   True    False   864.984  ...  \
579109  Autoroute du Nord    motorway   True    False   522.499  ...   
41800                 NaN       trunk   True    False  2565.566  ...   
569837                NaN    motorway   True    False  1618.600  ...   
569838                NaN    motorway   True    False   938.676  ...   
...                   ...         ...    ...      ...       ...  ...   
668691                NaN    tertiary  False    False    36.763  ...   
400380                NaN  trunk_link   True    False    36.853  ...   
400381     Route de Paris     primary   True    False    18.232  ...   
125491                NaN     primary  False     True   164.400  ...   
123852                NaN   secondary   True    False    35.410  ...   

       travel_time   bridge  maxspeed access    junction width tunnel service   
579108        24.0      NaN       130    NaN         NaN   NaN    NaN     NaN  \
579109        17.1      NaN       110    NaN         NaN   NaN    NaN     NaN   
41800         83.9      NaN       110    NaN         NaN   NaN    NaN     NaN   
569837        69.2      yes  [90, 70]    NaN         NaN   NaN    yes     NaN   
569838        48.2  viaduct        70    NaN         NaN   NaN    NaN     NaN   
...            ...      ...       ...    ...         ...   ...    ...     ...   
668691         2.1      NaN       NaN    NaN         NaN   NaN    NaN     NaN   
400380         4.4      NaN        30    NaN         NaN   NaN    NaN     NaN   
400381         1.0      NaN       NaN    NaN         NaN   NaN    NaN     NaN   
125491         9.2      NaN       NaN    NaN         NaN   NaN    NaN     NaN   
123852         2.4      NaN       NaN    NaN  roundabout   NaN    NaN     NaN   

       est_width area  
579108       NaN  NaN  
579109       NaN  NaN  
41800        NaN  NaN  
569837       NaN  NaN  
569838       NaN  NaN  
...          ...  ...  
668691       NaN  NaN  
400380       NaN  NaN  
400381       NaN  NaN  
125491       NaN  NaN  
123852       NaN  NaN  

[765823 rows x 21 columns]

In [36]:
print("conversion of objects to parameters list for neo4j...")

props_list = edges_reset.to_dict("records")

conversion of objects to parameters list for neo4j...


Pas de clé primaire, visiblement....

In [37]:
BATCH_SIZE = 20000

In [38]:
# --- Batch function ---

def batch(iterable, n=1):
    l = len(iterable)
    for ndx in range(0, l, n):
        yield iterable[ndx:min(ndx + n, l)]

In [46]:
with driver.session() as session:

    count_list = []

    # Batch the writing session :

    for props_batch in batch(props_list, BATCH_SIZE):

        start_time = time.time()

        result = session.execute_write(create_edge_between_ROAD_POINTS, props_batch)
        count_list.append(result[0]['COUNT'])
        nb_updates = sum(count_list)

        #total_index_batch = list(set([data['u'] for data in props_batch] + [data['v'] for data in props_batch]))

        print(f'Total Number of edges created : {nb_updates}...')

        #print("Fusion of nodes...")

        #c = 0

        #for index in total_index_batch:

            #result = session.execute_write(check_collection, index)

            #if result[0]['count(n)'] > 1:

            #c += 1

            #result = session.execute_write(all_fusion_nodes, index)

        #print(f"{c} nodes had to be merged...")
        print(f"Time for this batch : {time.time() - start_time}")



    driver.close()

print(f'Bath_list: {count_list}')

print(f'Total Numbers of nodes created/updates: {nb_updates}')

Total Number of edges created : 20000...
Time for this batch : 568.8676896095276
Total Number of edges created : 40000...
Time for this batch : 1951.6900656223297
Total Number of edges created : 60000...
Time for this batch : 3333.0931494235992
Total Number of edges created : 80000...
Time for this batch : 4857.215293884277
Total Number of edges created : 100000...
Time for this batch : 6109.667619943619
Total Number of edges created : 120000...
Time for this batch : 7216.066367387772


---

NODES FUSION

In [15]:
total_osmid = pd.DataFrame(pd.concat([edges_reset['u'], edges_reset['v']], axis=0))

In [19]:
total_osmid.value_counts()

831551001     22
476839818     20
447730712     20
440184953     18
1067837026    18
              ..
2413615787     2
2413750642     2
346661063      2
2413896930     2
539346248      2
Name: count, Length: 523308, dtype: int64

Tous les noeuds doivent être fusionnés sans exception. Effectivement, il n'y a pas de noeuds "impasse" ou orphelins.

In [27]:
def all_fusion_nodes(tx, id):

    query = "   WITH $id AS id \
                MATCH (n) \
                WHERE n.osmid = id \
                WITH collect(n) AS nodes \
                CALL apoc.refactor.mergeNodes( \
                                        nodes, \
                                        {properties: { \
                                        osmid: 'discard', \
                                        `.*`:'combine'} \
                                            }) \
                YIELD node \
                RETURN node "
    
    result = tx.run(query, id=id)
    return result.data()

In [24]:
nodes_reset = nodes.reset_index()

In [25]:
nodes_list = nodes_reset['osmid'].tolist()

In [28]:
with driver.session() as session:

    count_list = []

    # Batch the writing session :

    for i, node_id in enumerate(nodes_list):
        result = session.execute_write(all_fusion_nodes, node_id)
        if i%10000 == 0:
            print(f"{i+1} nodes fusion done...")

    driver.close()


1 nodes fusion done...


KeyboardInterrupt: 

------

MANIPULATION SUR FICHIER IMPORTE

Sur graph preexistant des points routiers, assignation des labels "ROAD_POINT" aux noeuds :

In [8]:
with driver.session() as session:

    result = session.execute_write(assign_label_ROAD_POINT)

    driver.close()

    print(result)


[{'count(n)': 523308}]
